# Workshop 6
## Carga de datos csv, shape y conversión de datos dataframe a geodataframe
1. Se cargan las librerías que se van a utilizar en el desarrollo del taller.
2. Se obtienen las rutas para cargar los archivos csv: el catálogo de estaciones, el diccionario de departamentos y las evas. De igual forma se carga el archivo *shape* de municipios.
3. Se reproyecta el *shape* de municipios al **ESPG : 9377**
4. Para el shape se renombran las columnas y se modifica la lectura del campo de código municipal y código de departamento para que se lea como *string* y que se mantengan los 5 caracteres.
5. Para el csv de evas también se renombran las columnas para evitar caracteres extraños e igualmente, se modifican las lecturas de los campos de código de departamento y municipio para que se lea como *string* y que se mantengan los 5 caracteres.
6. Para el csv **catálogo de estaciones IDEAM** se estraen los puntos de la columna **Ubicación**, se limpian de paréntesis, se separan en columnas *lat* y *lon* se convierten a *float*. Luego con la función *Point*, funcion acortada *lambda* y la función *GeoDataframe* se convierte a **Geodataframe**, determinando un **EPSG : 4326** a la geometría creada.
7. Se genera el mapa con los puntos de las estaciones con mapa base mediante la función *explore*.
8. Se reproyecta el sistema coordenado de las **estaciones** a un **EPSG : 9377**

In [1]:
#1 Carga de librerías
import geopandas as gpd
import pandas as pd
import matplotlib.pyplot as plt
import contextily as cx
from pathlib import Path
import pandas as pd
from shapely.geometry import Point

In [2]:

# Carga de archivos csv y shp - se imprimen listas de columnas e información de coordenadas del shp
archivos_CSV=r"/notebooks/Datos_Geograficos"
SHP=r"/notebooks/Datos_Geograficos/municipios_colombia"

shp_ruta=SHP+r"/municipios_colombia.shp"
muni_shp = gpd.read_file(shp_ruta)
muni_shp = muni_shp.to_crs(9377)

evas_ruta  = archivos_CSV+"/Evaluaciones_Agropecuarias_Municipales_EVA.csv"
evas = pd.read_csv(evas_ruta, encoding='utf-8')

estaciones_csv=archivos_CSV+"/Catalogo_Estaciones_IDEAM.csv"
estaciones = pd.read_csv(estaciones_csv, encoding='utf-8')

precip_csv = "/notebooks/precipitacion.csv"
precip = pd.read_csv(precip_csv,encoding='utf-8')


print("\nSISTEMA COORDENADO DEL SHP:\n", muni_shp.crs)

print('\n COLUMNAS DE PRECIPITACION\n',precip.columns.tolist())
print('\n COLUMNAS DE ESTACIONES\n',estaciones.columns.tolist())

#print('COLUMNAS DEL SHAPE \n',muni_shp.columns.tolist())
#print('COLUMNAS DEL CATALOGO DE ESTACIONES \n',estaciones.columns.tolist())
#print('COLUMNAS DE ARCHVIOS EVAS \n',evas.columns.tolist())

#print('\nDOS PRIMEROS DATOS ATRIBUTOS SHP\n',muni_shp.head(2))

# Renombra columnas y lectura de códigos de departamento y municipio - Shape 
muni_shp = muni_shp.rename(columns = {"DPTO_CCDGO":"DPTO_COD","MPIO_CCDGO":"MUN_COD","DPTO_CCDGO":"DPTO_COD","MPIO_CNMBR":"MPIO_NOM"}) # se renombran columnas
muni_shp['MUN_COD'] = muni_shp['MUN_COD'].astype(str).str.zfill(5) # leer columna de codigo municipal como texto y mantener los 5 caracteres siempre
muni_shp['DPTO_COD'] = muni_shp['DPTO_COD'].astype(str).str.zfill(5) # leer columna de codigo departamental como texto y mantener los 5 caracteres siempre
#print('COLUMNAS DEL SHAPE RENOMBRADAS\n',muni_shp.columns.tolist())

# Renombra columnas y lectura de códigos de departamento y municipio - csv EVAS 
evas = evas.rename(columns = {"CÓD. \nDEP.":"DPTO_COD","CÓD. MUN.":"MUN_COD","GRUPO \nDE CULTIVO":"GRUPO DE CULTIVO","SUBGRUPO \nDE CULTIVO":"SUBGRUPO DE CULTIVO",\
                       "Área Sembrada\n(ha)":"Área Sembrada (ha)","Área Cosechada\n(ha)":"Área Cosechada (ha)","Producción\n(t)":"Producción (t)",\
                      "Rendimiento\n(t/ha)":"Rendimiento (t/ha)","NOMBRE \nCIENTIFICO":"NOMBRE CIENTIFICO"})
evas['MUN_COD'] = evas ['MUN_COD'].astype(str).str.zfill(5)
evas['DPTO_COD'] = evas ['DPTO_COD'].astype(str).str.zfill(2)

print('\nCOLUMNAS DE EVAS RENOMBRADAS\n',evas.columns.tolist(),'\n')
#print('\n COLUMNAS DE SHP RENOMBRADAS\n',muni_shp.columns.tolist())
#print('\nDOS PRIMEROS DATOS ATRIBUTOS DE CATALOGO DE ESTACIONES\n',estaciones.head(2))

# Obtener las coordenadas de las estaciones y convertir a geometría de punto
estaciones[['lat','lon']] = estaciones['Ubicación'].str.strip("()").str.split(",",expand=True)
estaciones['lat'] = estaciones['lat'].astype(float)
estaciones['lon'] = estaciones['lon'].astype(float)
estaciones["geometry"] = estaciones.apply(lambda row: Point(row["lon"], row["lat"]), axis=1)
estaciones = gpd.GeoDataFrame(estaciones, geometry="geometry")

estaciones = estaciones.set_crs('epsg:4326')
estaciones.explore(width = '70%', height='70%')




SISTEMA COORDENADO DEL SHP:
 EPSG:9377

 COLUMNAS DE PRECIPITACION
 ['CodigoEstacion', 'NombreEstacion', 'Variable', 'Parametro', 'Fecha', 'Unidad', 'Valor', 'NivelAprobacion']

 COLUMNAS DE ESTACIONES
 ['Codigo', 'Nombre', 'Categoria', 'Estado', 'Departamento', 'Municipio', 'Ubicación', 'Altitud', 'Fecha_instalacion', 'Fecha_suspension', 'Corriente']

COLUMNAS DE EVAS RENOMBRADAS
 ['DPTO_COD', 'DEPARTAMENTO', 'MUN_COD', 'MUNICIPIO', 'GRUPO DE CULTIVO', 'SUBGRUPO DE CULTIVO', 'CULTIVO', 'DESAGREGACIÓN REGIONAL Y/O SISTEMA PRODUCTIVO', 'AÑO', 'PERIODO', 'Área Sembrada (ha)', 'Área Cosechada (ha)', 'Producción (t)', 'Rendimiento (t/ha)', 'ESTADO FISICO PRODUCCION', 'NOMBRE CIENTIFICO', 'CICLO DE CULTIVO'] 



In [3]:
# Reproyección de geodataframe de estaciones
estaciones = estaciones.to_crs(9377)
print("\nSISTEMA COORDENADO DE ESTACIONES:\n", estaciones.crs)



SISTEMA COORDENADO DE ESTACIONES:
 EPSG:9377


# PRUEBA PARA EL GITHUB